In [1]:
from tasho.templates.P2P import P2P
from tasho import TaskModel, default_mpc_options
from tasho.templates.Regularization import Regularization
from tasho.Variable import Variable
from tasho.ConstraintExpression import ConstraintExpression
from tasho.Expression import Expression
from tasho.MPC import MPC 
from tasho import environment as env
from tasho import WorldSimulator
from tasho.OCPGenerator import OCPGenerator
from robotshyu import Robot as rob
from time import sleep
import numpy as np
import casadi as cs
import pybullet as p
import tasho
import robotshyu
import os

pybullet build time: May 20 2022 19:44:17


In [2]:
# Options for example codes
frame_enable = True

# Ex1) P2P example

In [3]:
robot = rob.Robot("indy7")
link_name = 6
goal_pose = Variable(robot.name, "goal_pose", "magic_number", (4,4), np.array(
        [[0, 0, 1, 1], [0, 1, 0, -0.1], [-1, 0, 0, 0.6], [0, 0, 0, 1]]
    ))
q0 = [1.0, -0.05311582280659044, -0.815452580946695, -1.3191046402052224, -0.8582660722530533, 1.3988994390898029]

robot.set_joint_acceleration_limits(lb=-360*3.14159/180, ub=360*3.14159/180)
ndof = robot.nq
q_current = Variable(robot.name, "jointpos_init", 'magic_number', (ndof, 1), q0)

Loading robot params from json ...
Loaded 6-DoF robot: indy7


In [4]:
task_P2P = P2P(robot, link_name, goal_pose, q_current, 0.001)

In [5]:
task_P2P.write_task_graph("Indy7_P2P_Task.svg")

In [6]:
task_P2P.add_path_constraints(Regularization(task_P2P.variables['qd_'+robot.name], 1),
                              Regularization(task_P2P.variables['qdd_'+robot.name], 0.1))

In [7]:
task_P2P.write_task_graph("Indy7_P2P_Task2.svg")

In [8]:
horizon_steps = 10
horizon_period = 3.0
q_pred = [0]*horizon_steps

OCP_gen = OCPGenerator(task_P2P, False, {"time_period": horizon_period, "horizon_steps":horizon_steps})
q_ocp = OCP_gen.stage_tasks[0].variables['q_'+robot.name].x
OCP_gen.tc.set_initial(q_ocp, q0)
OCP_gen.tc.set_ocp_solver(
    "ipopt", 
    # {"ipopt":{"linear_solver":"ma27"}}
)
OCP_gen.tc.solve_ocp()


******************************************************************************
This program contains Ipopt, a library for large-scale nonlinear optimization.
 Ipopt is released as open source code under the Eclipse Public License (EPL).
         For more information visit http://projects.coin-or.org/Ipopt
******************************************************************************

This is Ipopt version 3.12.7, running with linear solver ma27.

Number of nonzeros in equality constraint Jacobian...:      452
Number of nonzeros in inequality constraint Jacobian.:      186
Number of nonzeros in Lagrangian Hessian.............:      141

Total number of variables............................:      192
                     variables with only lower bounds:        0
                variables with lower and upper bounds:        0
                     variables with only upper bounds:        0
Total number of equality constraints.................:      141
Total number of inequality constrai

In [9]:
t_grid, qsol = OCP_gen.tc.sol_sample(q_ocp)
_, q_dot_sol = OCP_gen.tc.sol_sample(OCP_gen.stage_tasks[0].variables['qd_'+robot.name].x)

obj = WorldSimulator.WorldSimulator()

# Add robot to the world environment
position = [0.0, 0.0, 0.0]
orientation = [0.0, 0.0, 0.0, 1.0]

robotID = obj.add_robot(position,orientation,robot_pkg=robot)
frameID0 = obj.add_robot(position,orientation,robot_pkg=robot,frame=True)
robotIDs=[robotID,frameID0]

if frame_enable:
    frameIDs = [0]*horizon_steps
    for i in range(horizon_steps):
        frameIDs[i] = obj.add_robot(position,orientation,robot_pkg=robot,frame=True)


for i in range(horizon_steps):
    q_pred[i]=qsol[i]

joint_indices = [0, 1, 2, 3, 4, 5]

obj.resetMultiJointState(robotIDs, joint_indices, [q0])

if frame_enable:
    obj.resetMultiJointState(frameIDs, joint_indices, [q0])
    obj.resetMultiJointState(frameIDs,joint_indices,q_pred)

In [10]:
for i in range(horizon_steps + 1):
    sleep(horizon_period*0.5/horizon_steps)
    obj.resetMultiJointState(
        robotIDs, joint_indices, [qsol[i]]
    )
    
sleep(0.5)
obj.end_simulation()

Ending simulation


# Ex2) Object picking MPC

In [3]:
robot = rob.Robot("indy7")
link_name = 6

# Define initial conditions of the robot
q0_val = [0, -0.423598, -0.9, 0.0, -1.5709, -0.523598]
qd0_val = [0] * robot.ndof

robot.set_joint_acceleration_limits(lb=-360*3.14159/180, ub=360*3.14159/180)

################################################
# Task spacification - Approximation to object
################################################

# Select prediction horizon and sample time for the MPC execution
horizon_size = 10
t_mpc = 0.05

q_init = Variable(robot.name, 'q_init', 'parameter', (robot.ndof,1))
qd_init = Variable(robot.name, 'qd_init', 'parameter', (robot.ndof,1))
goal_pose = Variable(robot.name, "goal_pose", 'parameter', (4,4))

task_P2P = P2P(robot, link_name, goal_pose, q_init, 0.001)
task_P2P.write_task_graph("Indy7_P2P_Task4.svg")

Loading robot params from json ...
Loaded 6-DoF robot: indy7


In [4]:
task_P2P.remove_initial_constraints(task_P2P.constraint_expressions['stationary_qd_indy7'])
task_P2P.remove_terminal_constraints('rot_con_pose_6_indy7_vs_goal',
                                    'trans_con_pose_6_indy7_vs_goal')
task_P2P.write_task_graph("Indy7_P2P_Task5.svg")

In [5]:
task_P2P.add_initial_constraints(ConstraintExpression(robot.name, "eq", Expression(robot.name, "err_qd_qinit", lambda a, b : a - b, qd_init, task_P2P.variables['qd_indy7']),
                             "hard", reference = 0))
task_P2P.add_path_constraints(Regularization(task_P2P.expressions['trans_error_pose_6_indy7_vs_goal'], 5e0, norm = "L1"),
                            Regularization(task_P2P.expressions['ax_ang_error_pose_6_indy7_vs_goal'], 1e0), 
                            Regularization(task_P2P.variables['qd_indy7'], 1e-1),
                            Regularization(task_P2P.variables['qdd_indy7'], 1e-3))

task_P2P.write_task_graph("Indy7_P2P_Task6.svg")

In [6]:
pOCP = OCPGenerator(task_P2P, False, {"time_period":horizon_size*t_mpc, "horizon_steps":horizon_size})

tc = pOCP.tc

################################################
# Set solver and discretization options
################################################
tc.set_ocp_solver("ipopt", {"ipopt": {"print_level": 5,"tol": 1e-3}})
# tc.set_ocp_solver("ipopt", {"ipopt": {"print_level": 0,"tol": 1e-3, "linear_solver":"ma27"}}) #use this if you have hsl


################################################
# Set parameter values
################################################
q = pOCP.stage_tasks[0].variables['q_indy7'].x
qd = pOCP.stage_tasks[0].variables['qd_indy7'].x
q_0 = pOCP.stage_tasks[0].variables['q_init_indy7'].x
qd_0 = pOCP.stage_tasks[0].variables['qd_init_indy7'].x
goal_pose = pOCP.stage_tasks[0].variables['goal_pose_indy7'].x
goal_pose_val =  cs.vertcat(
    cs.hcat([-1, 0, 0, 0.5]),
    cs.hcat([0, 1, 0, 0.0]),
    cs.hcat([0, 0, -1, 0.25]),
    cs.hcat([0, 0, 0, 1]),
)
tc.set_initial(q, q0_val)
tc.set_value(goal_pose, goal_pose_val)
tc.set_value(q_0, q0_val)
tc.set_value(qd_0, qd0_val)

# Add an output port for joint velocities as well
tc.tc_dict["out_ports"].append({"name":"port_out_qd_indy7", "var":"qd_indy7", "desc": "output port for the joint velocities"})

# Add a monitor for termination criteria
tc.add_monitor({"name":"termination_criteria", "expression":cs.sqrt(cs.sumsqr(pOCP.stage_tasks[0].expressions["trans_error_pose_6_indy7_vs_goal"].x)) - 2e-2, "reference":0, "lower":True, "initial":True})

mpc_options = default_mpc_options.get_default_mpc_options()


tc.ocp_solver = "ipopt"
tc.ocp_options = mpc_options["ipopt"]["options"]
tc.mpc_solver = tc.ocp_solver
tc.mpc_options = tc.ocp_options
tc.set_ocp_solver("ipopt", tc.mpc_options)
os.system("export OMP_NUM_THREADS = 1")

sol = tc.solve_ocp()


******************************************************************************
This program contains Ipopt, a library for large-scale nonlinear optimization.
 Ipopt is released as open source code under the Eclipse Public License (EPL).
         For more information visit http://projects.coin-or.org/Ipopt
******************************************************************************

      solver  :   t_proc      (avg)   t_wall      (avg)    n_eval
       nlp_f  |  76.00us ( 25.33us)  76.11us ( 25.37us)         3
       nlp_g  |  26.00us (  8.67us)  25.62us (  8.54us)         3
    nlp_grad  |  86.00us ( 86.00us)  86.17us ( 86.17us)         1
  nlp_grad_f  | 204.00us ( 68.00us) 203.40us ( 67.80us)         3
  nlp_hess_l  | 646.00us (323.00us) 645.89us (322.95us)         2
   nlp_jac_g  |  36.00us ( 12.00us)  35.70us ( 11.90us)         3
       total  |   3.76ms (  3.76ms)   3.74ms (  3.74ms)         1


sh: 1: export: : bad variable name


In [7]:
dir_casadi_func = "casadi_dir"
os.makedirs("./"+dir_casadi_func, exist_ok=True)
vars_db = tc.generate_MPC_component("./"+dir_casadi_func+"/", {"ocp_cg_opts":{"save":True, "codegen":False, "jit":False}, "mpc":True, "mpc_cg_opts":{"save":True, "codegen":False, "jit":False}})

@1=(opti0_p_2[12:15]-fk_T(opti0_x_1){6}[12:15]), (sqrt(dot(@1, @1))-0.02)
@1=(opti0_p_2[12:15]-fk_T(opti0_x_1){6}[12:15]), (sqrt(dot(@1, @1))-0.02)


In [8]:
MPC_component = MPC("indy7_obj_pickup", "./"+dir_casadi_func+"/"+ tc.name + ".json")

In [9]:
obj = WorldSimulator.WorldSimulator(bullet_gui=True)

# Add robot to the world environment
position = [0.0, 0.0, 0.0]
orientation = [0.0, 0.0, 0.0, 1.0]

robotID = obj.add_robot(position,orientation,robot_pkg=robot)

if frame_enable:
    frameIDs = [0]*horizon_size
    for i in range(horizon_size):
        frameIDs[i] = obj.add_robot(position,orientation,robot_pkg=robot,frame=True)

# Set environment
environment = env.Environment()
package_path = tasho.__path__[0]
cube1 = env.Cube(length = 1, position = [0.5, -0.2, 0.35], orientation = [0.0, 0.0, 0.0, 1.0], urdf = package_path+"/models/objects/cube_small.urdf")
environment.add_object(cube1, "cube")
table1 = env.Box(height = 0.3, position = [0.5, 0, 0], orientation = [0.0, 0.0, 0.7071080798594737, 0.7071054825112364], urdf =package_path+ "/models/objects/table.urdf")
environment.add_object(table1, "table1")

cube2 = env.Cube(length = 1, position = [0.5, -0.2, 0.35], orientation = [0.0, 0.0, 0.0, 1.0], urdf = package_path+"/models/objects/cube_small_col.urdf", fixed = True)
environment.add_object(cube2, "cube2")
environment.set_in_world_simulator(obj)
cubeID = environment.get_object_ID("cube")
cube2ID = environment.get_object_ID("cube2")

p.resetBaseVelocity(cubeID, linearVelocity=[0, 0.8, 0])
# Determine number of samples that the simulation should be executed
no_samples = int(t_mpc / obj.physics_ts)
if no_samples != t_mpc / obj.physics_ts:
    print("[ERROR] MPC sampling time not integer multiple of physics sampling time")

# Correspondence between joint numbers in bullet and OCP
joint_indices = [0, 1, 2, 3, 4, 5]

 # Begin the visualization by applying the initial control signal
ts, q_sol = tc.sol_sample(q, grid="control")
ts, q_dot_sol = tc.sol_sample(qd, grid="control")

obj.resetJointState(robotID,joint_indices,q0_val)
if frame_enable==True:
    obj.resetMultiJointState(frameIDs, joint_indices, [q0_val])

obj.setController(
    robotID, "velocity", joint_indices, targetVelocities=q_dot_sol[0]
)
q_log = []
q_dot_log = []
predicted_pos_log = []
q_pred = [0]*horizon_size


In [10]:
# Execute the MPC loop

for i in range(horizon_size * 30):
    print("----------- MPC execution -----------")

    q_now = obj.readJointPositions(robotID, joint_indices)
    qd_now = obj.readJointVelocities(robotID, joint_indices)
        
    MPC_component.input_ports["port_inp_q_init_indy7"]["val"] = q_now
    MPC_component.input_ports["port_inp_qd_init_indy7"]["val"] = qd_now

    # Predict the position of the target object (cube)
    lin_vel, ang_vel = p.getBaseVelocity(cubeID)
    lin_vel = cs.DM(lin_vel)
    lin_pos, _ = p.getBasePositionAndOrientation(cubeID)
    lin_pos = cs.DM(lin_pos)
    time_to_stop = cs.norm_1(lin_vel) / 0.3
    predicted_pos = (
        cs.DM(lin_pos)
        + cs.DM(lin_vel) * time_to_stop
        - 0.5 * 0.5 * lin_vel / (cs.norm_1(lin_vel) + 1e-3) * time_to_stop ** 2
    )
    predicted_pos_log.append(predicted_pos.full())
    p.resetBasePositionAndOrientation(cube2ID, predicted_pos.full(), [0.0, 0.0, 0.0, 1.0])
    predicted_pos[2] += 0.06  # cube height
    print("Predicted position of cube", predicted_pos)
    predicted_pos_val = cs.vertcat(
        cs.hcat([-1, 0, 0, predicted_pos[0]]),
        cs.hcat([0, 1, 0, predicted_pos[1]]),
        cs.hcat([0, 0, -1, predicted_pos[2]]),
        cs.hcat([0, 0, 0, 1]),
    )

    MPC_component.input_ports["port_inp_goal_pose_indy7"]["val"] = cs.vec(predicted_pos_val)
        
    if i == 0:
        MPC_component.configMPC()

    MPC_component.runMPC()
    if frame_enable==True:
        sol = MPC_component.res_vals
        print(sol)
        for i in range(horizon_size):
            q_pred[i]=sol[robot.ndof*i:robot.ndof*i+robot.ndof].full()
            print(q_pred)
        obj.resetMultiJointState(frameIDs, joint_indices, q_pred)

    q_log.append(q_now)
    q_dot_log.append(qd_now)

    # Set control signal to the simulated robot
    qd_control_sig = MPC_component.output_ports["port_out_qd_indy7"]["val"].full()
    qdd_control_sig = (MPC_component.output_ports["port_out_qdd_indy7"]["val"] * t_mpc).full()
    
    obj.setController(
        robotID, "velocity", joint_indices, targetVelocities=qd_control_sig+qdd_control_sig
    )
    
    # Simulate
    obj.run_simulation(no_samples)

    # Termination criteria
#     if "termination_criteria_true" in MPC_component.event_output_port:
#         break

----------- MPC execution -----------
Predicted position of cube [0.5, 0.15777500346789, 0.41]
startThreads creating 1 threads.
starting thread 0
started thread 0 
argc=2
argv[0] = --unused
argv[1] = --start_demo_name=Physics Server
ExampleBrowserThreadFunc started
X11 functions dynamically loaded using dlopen/dlsym OK!
X11 functions dynamically loaded using dlopen/dlsym OK!
Creating context
Created GL 3.3 context
Direct GLX rendering context obtained
Making context current
GL_VENDOR=Mesa/X.org
GL_RENDERER=llvmpipe (LLVM 12.0.0, 256 bits)
GL_VERSION=4.5 (Core Profile) Mesa 21.2.6
GL_SHADING_LANGUAGE_VERSION=4.50
pthread_getconcurrency()=0
Version = 4.5 (Core Profile) Mesa 21.2.6
Vendor = Mesa/X.org
Renderer = llvmpipe (LLVM 12.0.0, 256 bits)
b3Printf: Selected demo: Physics Server
startThreads creating 1 threads.
starting thread 0
started thread 0 
MotionThreadFunc thread started
ven = Mesa/X.org
ven = Mesa/X.org
      solver  :   t_proc      (avg)   t_wall      (avg)    n_eval
       

----------- MPC execution -----------
Predicted position of cube [0.5, 0.90957753618168, -1.5356369164058]
      solver  :   t_proc      (avg)   t_wall      (avg)    n_eval
       nlp_f  | 356.00us ( 29.67us) 356.77us ( 29.73us)        12
       nlp_g  |  97.00us (  8.08us)  95.04us (  7.92us)        12
    nlp_grad  | 103.00us (103.00us) 103.22us (103.22us)         1
  nlp_grad_f  |   8.88ms (739.92us) 901.22us ( 75.10us)        12
  nlp_hess_l  |  16.07ms (  1.46ms)   4.24ms (385.60us)        11
   nlp_jac_g  | 162.00us ( 13.50us) 160.48us ( 13.37us)        12
       total  |  57.33ms ( 57.33ms)  16.40ms ( 16.40ms)         1
[0.082910235488029, -0.49931277363048, -0.97124996908904, 0.076562513880503, -1.5758450657204, -0.41693648283054, 0.13152518134383, -0.54825559111795, -1.0146603415757, 0.12305538007842, -1.5499348718226, -0.36866658718959, 0.1815174636619, -0.59825276087955, -1.0646507052049, 0.17304602058617, -1.5031187679392, -0.31878516476842, 0.2315081672044, -0.648249396099

----------- MPC execution -----------
Predicted position of cube [0.49999970393311, 0.24876619450623, 0.27315802591234]
      solver  :   t_proc      (avg)   t_wall      (avg)    n_eval
       nlp_f  | 123.00us ( 30.75us) 122.91us ( 30.73us)         4
       nlp_g  |   4.52ms (  1.13ms)  37.93us (  9.48us)         4
    nlp_grad  | 104.00us (104.00us) 103.37us (103.37us)         1
  nlp_grad_f  | 296.00us ( 74.00us) 297.57us ( 74.39us)         4
  nlp_hess_l  |   7.53ms (  2.51ms)   1.24ms (414.49us)         3
   nlp_jac_g  |  56.00us ( 14.00us)  55.60us ( 13.90us)         4
       total  |  26.93ms ( 26.93ms)   5.70ms (  5.70ms)         1
[0.22437942040197, -0.63316445217177, -1.1063056516711, 0.21396252539482, -1.4871231129975, -0.27131359304992, 0.26261008484576, -0.65958417662719, -1.1349394984284, 0.24537338320326, -1.4652986865126, -0.22150436396523, 0.29474155281823, -0.67405415662011, -1.1530732098988, 0.26658624882235, -1.4442004686741, -0.17223374142285, 0.32155601794168, -0.

----------- MPC execution -----------
Predicted position of cube [0.49999970012609, 0.28460141456194, 0.2725184405636]
      solver  :   t_proc      (avg)   t_wall      (avg)    n_eval
       nlp_f  |  88.00us ( 29.33us)  87.56us ( 29.19us)         3
       nlp_g  |  32.00us ( 10.67us)  31.82us ( 10.61us)         3
    nlp_grad  |   1.18ms (  1.18ms) 103.95us (103.95us)         1
  nlp_grad_f  | 745.00us (248.33us) 292.09us ( 97.36us)         3
  nlp_hess_l  | 774.00us (387.00us) 775.02us (387.51us)         2
   nlp_jac_g  |  90.00us ( 30.00us)  53.73us ( 17.91us)         3
       total  |  20.56ms ( 20.56ms)   4.68ms (  4.68ms)         1
[0.3328514512199, -0.6961088307407, -1.1812437493206, 0.2953797135722, -1.4033327957151, -0.12218882733889, 0.36468126718195, -0.70555037854828, -1.1965229799481, 0.3120116688072, -1.3770989607466, -0.073341256234462, 0.39282857910205, -0.70751249003274, -1.2047952872671, 0.32051692769972, -1.3548080698698, -0.026916492707726, 0.41714154889762, -0.705

----------- MPC execution -----------
Predicted position of cube [0.499999682618, 0.31677327478954, 0.2724911803854]
      solver  :   t_proc      (avg)   t_wall      (avg)    n_eval
       nlp_f  |  90.00us ( 30.00us)  90.05us ( 30.02us)         3
       nlp_g  |  37.00us ( 12.33us)  35.83us ( 11.94us)         3
    nlp_grad  | 102.00us (102.00us) 102.34us (102.34us)         1
  nlp_grad_f  | 226.00us ( 75.33us) 226.36us ( 75.45us)         3
  nlp_hess_l  |   6.04ms (  3.02ms) 813.75us (406.87us)         2
   nlp_jac_g  |  42.00us ( 14.00us)  42.27us ( 14.09us)         3
       total  |  16.36ms ( 16.36ms)   3.96ms (  3.96ms)         1
[0.42239570831643, -0.70942717389103, -1.2107083874579, 0.32907059068021, -1.3383486780064, 0.021686290454208, 0.45033252368598, -0.70878132215606, -1.2151471400307, 0.33292648270665, -1.3200064543433, 0.067062493169158, 0.47631299766486, -0.70590660895855, -1.2169937657918, 0.33194206392346, -1.3041881715409, 0.10878616286789, 0.49941415016224, -0.7023

...

----------- MPC execution -----------
Predicted position of cube [0.49999413973103, 0.43632680991963, 0.084989999999997]
      solver  :   t_proc      (avg)   t_wall      (avg)    n_eval
       nlp_f  |  93.00us ( 31.00us)  93.48us ( 31.16us)         3
       nlp_g  |  32.00us ( 10.67us)  30.65us ( 10.22us)         3
    nlp_grad  | 106.00us (106.00us) 106.67us (106.67us)         1
  nlp_grad_f  | 241.00us ( 80.33us) 242.13us ( 80.71us)         3
  nlp_hess_l  | 794.00us (397.00us) 796.08us (398.04us)         2
   nlp_jac_g  |  46.00us ( 15.33us)  42.92us ( 14.31us)         3
       total  |  12.09ms ( 12.09ms)   4.45ms (  4.45ms)         1
[1.0018914072944, -0.99053365547752, -1.3088034801659, 0.0011657918093401, -0.84294338997836, 1.0009732574683, 1.0018960341994, -0.99052469920955, -1.3088319874546, 0.001156552383746, -0.84291723743895, 1.0009848589836, 1.0019004196389, -0.99051616979923, -1.3088590436127, 0.0011476147790276, -0.84289237578792, 1.0009958714286, 1.0019043861676, -0.9

----------- MPC execution -----------
Predicted position of cube [0.49999413973103, 0.43632680991963, 0.084989999999997]
      solver  :   t_proc      (avg)   t_wall      (avg)    n_eval
       nlp_f  | 336.00us (112.00us) 104.06us ( 34.69us)         3
       nlp_g  | 104.00us ( 34.67us)  44.99us ( 15.00us)         3
    nlp_grad  | 428.00us (428.00us) 102.46us (102.46us)         1
  nlp_grad_f  | 538.00us (179.33us) 255.96us ( 85.32us)         3
  nlp_hess_l  | 789.00us (394.50us) 789.73us (394.86us)         2
   nlp_jac_g  |  45.00us ( 15.00us)  45.09us ( 15.03us)         3
       total  |  17.53ms ( 17.53ms)   4.63ms (  4.63ms)         1
[1.0019050784771, -0.9905072160587, -1.308887779394, 0.0011387776497517, -0.84286603360841, 1.0010075649299, 1.0019095071135, -0.9904986416873, -1.3089150722034, 0.0011299149304804, -0.84284096280159, 1.0010186774884, 1.0019137043967, -0.9904904744277, -1.3089409763916, 0.0011213349509204, -0.84281712700742, 1.0010292257025, 1.0019174995283, -0.9904

----------- MPC execution -----------
Predicted position of cube [0.49999413973103, 0.43632680991963, 0.084989999999997]
      solver  :   t_proc      (avg)   t_wall      (avg)    n_eval
       nlp_f  | 660.00us (220.00us)  89.61us ( 29.87us)         3
       nlp_g  |  35.00us ( 11.67us)  34.30us ( 11.43us)         3
    nlp_grad  |   1.00ms (  1.00ms) 103.52us (103.52us)         1
  nlp_grad_f  |   2.35ms (784.67us) 231.62us ( 77.21us)         3
  nlp_hess_l  |   3.10ms (  1.55ms) 805.43us (402.71us)         2
   nlp_jac_g  |  41.00us ( 13.67us)  41.30us ( 13.77us)         3
       total  |  20.13ms ( 20.13ms)   3.71ms (  3.71ms)         1
[1.0019181637201, -0.99048190471388, -1.3089684907494, 0.0011128768678728, -0.84279187265806, 1.0010404270517, 1.0019224028019, -0.99047369494715, -1.3089946236574, 0.0011043744693889, -0.84276783468368, 1.0010510718264, 1.0019264202035, -0.9904658734328, -1.3090194276551, 0.0010961365589873, -0.84274497838095, 1.0010611759203, 1.0019300514792, -0.9

----------- MPC execution -----------
Predicted position of cube [0.49999413973103, 0.43632680991963, 0.084989999999997]
      solver  :   t_proc      (avg)   t_wall      (avg)    n_eval
       nlp_f  |  96.00us ( 32.00us)  96.12us ( 32.04us)         3
       nlp_g  |  73.00us ( 24.33us)  26.61us (  8.87us)         3
    nlp_grad  | 105.00us (105.00us) 104.94us (104.94us)         1
  nlp_grad_f  | 237.00us ( 79.00us) 236.62us ( 78.87us)         3
  nlp_hess_l  | 836.00us (418.00us) 838.25us (419.13us)         2
   nlp_jac_g  |  61.00us ( 20.33us)  60.92us ( 20.31us)         3
       total  |  11.01ms ( 11.01ms)   4.54ms (  4.54ms)         1
[1.0019306887846, -0.9904576703494, -1.309045775484, 0.0010880410395349, -0.84272076270022, 1.0010719064374, 1.001934746651, -0.990449808666, -1.3090708006487, 0.0010798832907454, -0.84269771089477, 1.0010821036994, 1.0019385920891, -0.99044231723251, -1.3090945539233, 0.0010719725717341, -0.84267578981698, 1.0010917829246, 1.0019420667245, -0.99043

----------- MPC execution -----------
Predicted position of cube [0.49999413973103, 0.43632680991963, 0.084989999999997]
      solver  :   t_proc      (avg)   t_wall      (avg)    n_eval
       nlp_f  |  99.00us ( 33.00us) 100.22us ( 33.41us)         3
       nlp_g  |  38.00us ( 12.67us)  37.19us ( 12.40us)         3
    nlp_grad  |  91.00us ( 91.00us)  90.67us ( 90.67us)         1
  nlp_grad_f  | 253.00us ( 84.33us) 254.23us ( 84.74us)         3
  nlp_hess_l  |   6.53ms (  3.26ms) 935.58us (467.79us)         2
   nlp_jac_g  |  45.00us ( 15.00us)  44.28us ( 14.76us)         3
       total  |  10.14ms ( 10.14ms)   4.54ms (  4.54ms)         1
[1.0019426783223, -0.99043446416805, -1.3091197876715, 0.001064223847327, -0.84265256585771, 1.0011020630195, 1.0019465629524, -0.99042693480563, -1.309143754899, 0.0010563957607925, -0.84263045564926, 1.0011118321721, 1.001950244002, -0.9904197584974, -1.3091665047091, 0.0010487980076953, -0.8426094275401, 1.001121104954, 1.0019535689002, -0.990413

In [12]:
obj.end_simulation()

max(MPC_component.solver_times)

Ending simulation


0.01711273193359375

In [13]:
qd_control_sig+qdd_control_sig

array([[ 7.66154574e-05],
       [ 1.48693177e-04],
       [-4.72362471e-04],
       [-1.56550123e-04],
       [ 4.36071320e-04],
       [ 1.92589937e-04]])